In [4]:
%%sh
pip install kaggle --upgrade

  Created wheel for kaggle: filename=kaggle-1.5.12-py3-none-any.whl size=73053 sha256=b6e44ad185decb8af7325d1cbdbd432239c4f8d3ff49161a0ea6922b4d7a651c
  Stored in directory: /home/ec2-user/.cache/pip/wheels/77/47/e4/44a4ba1b7dfd53faaa35f59f1175e123b213ff401a8a56876b
  Created wheel for python-slugify: filename=python_slugify-4.0.1-py2.py3-none-any.whl size=6769 sha256=2d3ebd3ea5321b089ac67ab3b863da0cf3c19031b089331d393717846a01843e
  Stored in directory: /home/ec2-user/.cache/pip/wheels/72/e6/db/122611605e60148f54ee2abaca98b2bbeafc6e22486a867bad
Successfully built kaggle python-slugify


In [25]:
# Was downloading this previously if kaggle is not be involved!
# !wget --no-check-certificate https://storage.googleapis.com/mledu-datasets/cats_and_dogs_filtered.zip

In [154]:
%%sh
kaggle --version

Kaggle API 1.5.12


In [155]:
%%sh
kaggle competitions download -c dogs-vs-cats
unzip dogs-vs-cats.zip
unzip train.zip


Archive:  dogs-vs-cats.zip
  inflating: sampleSubmission.csv    
  inflating: test1.zip               
  inflating: train.zip               
Archive:  train.zip
   creating: train/
  inflating: train/cat.0.jpg         
  inflating: train/cat.1.jpg         
  inflating: train/cat.10.jpg        
  inflating: train/cat.100.jpg       
  inflating: train/cat.1000.jpg      
  inflating: train/cat.10000.jpg     
  inflating: train/cat.10001.jpg     
  inflating: train/cat.10002.jpg     
  inflating: train/cat.10003.jpg     
  inflating: train/cat.10004.jpg     
  inflating: train/cat.10005.jpg     
  inflating: train/cat.10006.jpg     
  inflating: train/cat.10007.jpg     
  inflating: train/cat.10008.jpg     
  inflating: train/cat.10009.jpg     
  inflating: train/cat.1001.jpg      
  inflating: train/cat.10010.jpg     
  inflating: train/cat.10011.jpg     
  inflating: train/cat.10012.jpg     
  inflating: train/cat.10013.jpg     
  inflating: train/cat.10014.jpg     
  inflating: train/c

100%|██████████| 812M/812M [00:10<00:00, 81.4MB/s]


In [156]:
!cd train
!mkdir dog cat
!find . -name 'dog.*' -exec mv {} dog \;
!find . -name 'cat.*' -exec mv {} cat \;

find: `./lost+found': Permission denied
find: `./lost+found': Permission denied
mv: ‘./cat/cat.1054.jpg’ and ‘cat/cat.1054.jpg’ are the same file
mv: ‘./cat/cat.1202.jpg’ and ‘cat/cat.1202.jpg’ are the same file
mv: ‘./cat/cat.6494.jpg’ and ‘cat/cat.6494.jpg’ are the same file
mv: ‘./cat/cat.5753.jpg’ and ‘cat/cat.5753.jpg’ are the same file
mv: ‘./cat/cat.956.jpg’ and ‘cat/cat.956.jpg’ are the same file
mv: ‘./cat/cat.5481.jpg’ and ‘cat/cat.5481.jpg’ are the same file
mv: ‘./cat/cat.9875.jpg’ and ‘cat/cat.9875.jpg’ are the same file
mv: ‘./cat/cat.7605.jpg’ and ‘cat/cat.7605.jpg’ are the same file
mv: ‘./cat/cat.1327.jpg’ and ‘cat/cat.1327.jpg’ are the same file
mv: ‘./cat/cat.9716.jpg’ and ‘cat/cat.9716.jpg’ are the same file
mv: ‘./cat/cat.6549.jpg’ and ‘cat/cat.6549.jpg’ are the same file
mv: ‘./cat/cat.11153.jpg’ and ‘cat/cat.11153.jpg’ are the same file
mv: ‘./cat/cat.6061.jpg’ and ‘cat/cat.6061.jpg’ are the same file
mv: ‘./cat/cat.10837.jpg’ and ‘cat/cat.10837.jpg’ are the same

In [166]:
!mv cat train

In [169]:
!mv dog train

In [174]:
!ls train/cat -1 | wc -l

12500


In [175]:
%%sh
ls train/dog -1 | wc -l

12500


## Using bash scripting for moving 1250 random dog images and 1250 random cats images to specific directories for validation images:

In [176]:
!mkdir -p val/dog val/cat

In [179]:
!ls train/dog | sort -R | tail -1250 | while read file; do mv train/dog/$file val/dog; done

In [182]:
!ls train/cat | sort -R | tail -1250 | while read file; do mv train/cat/$file val/cat; done

## Reconfirming the above commands:

In [197]:
!ls val/dog -1 | wc -l

1250


In [198]:
!ls val/cat -1 | wc -l

1250


In [190]:
# Command for finding the number of files in a directory:
!ls -a val/dog -1 | wc -l

1252


## 22,500 images in the training folder:

In [196]:
!ls train/dog -1 | wc -l

11250


In [195]:
!ls train/cat -1 | wc -l

11250


In [200]:
!du -h

289M	./train/dog
248M	./train/cat
538M	./train
4.0K	./.sparkmagic
32M	./val/dog
27M	./val/cat
59M	./val
du: cannot read directory ‘./lost+found’: Permission denied
16K	./lost+found
2.3M	./.ipynb_checkpoints
2.2G	.


## Installing two dependencies of im2rec:

In [202]:
!wget https://raw.githubusercontent.com/apache/incubator-mxnet/master/tools/im2rec.py

--2021-04-04 15:27:09--  https://raw.githubusercontent.com/apache/incubator-mxnet/master/tools/im2rec.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.110.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 15838 (15K) [text/plain]
Saving to: ‘im2rec.py’

im2rec.py           100%[===================>]  15.47K  --.-KB/s    in 0.001s  

2021-04-04 15:27:10 (26.5 MB/s) - ‘im2rec.py’ saved [15838/15838]



In [203]:
!pip install mxnet opencv-python

     |████████████████████████████████| 46.9 MB 264 kB/s eta 0:00:01


## Running im2rec to build two files - one for training and one for validation: 

In [204]:
!python3 im2rec.py --list --recursive dogscats-train train

cat 0
dog 1


In [205]:
!python3 im2rec.py --list --recursive dogscats-val val

cat 0
dog 1


The .lst file created has three columns which are:
1. Unique Image Identifier [e.g. 3197];
2. Class label (0 for cats, 1 for dogs) [e.g. 0.000000];
3. The image path [cat/cat.1625.jpg].

## Moving list files to specific directories so they can be passed to the estimator as two new channels:

In [206]:
mkdir train_lst val_lst

In [207]:
mv dogscats-train.lst train_lst

In [208]:
mv dogscats-val.lst val_lst

In [212]:
!du -h

289M	./train/dog
248M	./train/cat
538M	./train
4.0K	./.sparkmagic
80K	./val_lst
32M	./val/dog
27M	./val/cat
59M	./val
du: cannot read directory ‘./lost+found’: Permission denied
16K	./lost+found
700K	./train_lst
2.3M	./.ipynb_checkpoints
2.2G	.


## Syncing the four folders to the SageMaker default bucket: 

In [213]:
# getting the default bucket:
import sagemaker
sess = sagemaker.Session()
bucket = sess.default_bucket()

In [214]:
print(bucket)

sagemaker-us-east-2-181081383695


In [228]:
import awscli

In [225]:
!aws --version

aws-cli/1.19.39 Python/3.6.13 Linux/4.14.225-121.362.amzn1.x86_64 botocore/1.20.39


In [237]:
!aws s3 sync train s3://sagemaker-us-east-2-181081383695/dogscats-images/input/

upload: train/cat/cat.1.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.1.jpg
upload: train/cat/cat.1000.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.1000.jpg
upload: train/cat/cat.0.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.0.jpg
upload: train/cat/cat.10003.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10003.jpg
upload: train/cat/cat.10001.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10001.jpg
upload: train/cat/cat.10010.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10010.jpg
upload: train/cat/cat.10012.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10012.jpg
upload: train/cat/cat.1001.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.1001.jpg
upload: train/cat/cat.10013.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10013.jpg
upl

In [238]:
!aws s3 sync val s3://sagemaker-us-east-2-181081383695/dogscats-images/input/

upload: val/cat/cat.10016.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10016.jpg
upload: val/cat/cat.10011.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10011.jpg
upload: val/cat/cat.10034.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10034.jpg
upload: val/cat/cat.10046.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10046.jpg
upload: val/cat/cat.10060.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10060.jpg
upload: val/cat/cat.10052.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10052.jpg
upload: val/cat/cat.10043.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10043.jpg
upload: val/cat/cat.1016.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.1016.jpg
upload: val/cat/cat.10078.jpg to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/cat/cat.10078.jpg
upl

In [239]:
!aws s3 sync train_lst s3://sagemaker-us-east-2-181081383695/dogscats-images/input/

upload: train_lst/dogscats-train.lst to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/dogscats-train.lst


In [240]:
!aws s3 sync val_lst s3://sagemaker-us-east-2-181081383695/dogscats-images/input/

upload: val_lst/dogscats-val.lst to s3://sagemaker-us-east-2-181081383695/dogscats-images/input/dogscats-val.lst


In [245]:
!aws s3 ls s3://sagemaker-us-east-2-181081383695/dogscats-images/input/

                           PRE cat/
                           PRE dog/
2021-04-04 16:06:11     711408 dogscats-train.lst
2021-04-04 16:07:28      76652 dogscats-val.lst
